In [ ]:
!pip install transformers
from transformers import BertTokenizer, BertForTokenClassification
import torch
from google.colab import drive
drive.mount('/content/drive', force_remount=True)
import csv
import re
import pandas as pd


     |████████████████████████████████| 757kB 4.0MB/s 
     |████████████████████████████████| 1.1MB 16.4MB/s 
     |████████████████████████████████| 890kB 30.5MB/s 
     |████████████████████████████████| 3.0MB 39.1MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893260 sha256=5e2c889caa1c589763e56fa7fb6142746471a506b03288e8dac10c5c7f602422
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses
Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your 

In [ ]:
def slideWindow(stride,w_size,x,y):
    x_list = []
    y_list = []
    s_idx = 0
    while (s_idx+w_size)<len(x):
      x_list.append(x[s_idx:(s_idx+w_size)])
      y_list.append(y[s_idx:(s_idx+w_size)])
      s_idx = s_idx+stride
    if(s_idx<len(x)):
      x_list.append(x[s_idx:])
      y_list.append(y[s_idx:])
    return x_list , y_list
def slideWindow1(stride,w_size,x):
    x_list = []
    s_idx = 0
    while (s_idx+w_size)<len(x):
      x_list.append(x[s_idx:(s_idx+w_size)])
      s_idx = s_idx+stride
    if(s_idx<len(x)):
      x_list.append(x[s_idx:])
    return x_list

In [ ]:
def train(model,input,label,EPOCHS,is_slide =True):
  
  model.train()

  optimizer = torch.optim.Adam(model.parameters(), lr=1e-5)
  device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
  model.to(device)
  for epoch in range(EPOCHS):
      print("epoch",epoch)
      running_loss = 0.0
      for idx in range(len(input)):
          input_data = input[idx]
          label_data = label[idx]
          label_data = [int(char) for char in label_data]
          tokens = tokenizer.tokenize(input_data)
          print(tokens,'i am tokenizer')

          print(idx)
          if(is_slide):
            b_x,b_y = slideWindow(256,512,tokens,label_data)
          else:
            #b_x ,b_y = [input_data[10:110]] , [label_data[10:110]]
            b_x ,b_y = [tokens[15:115]] , [tokens[15:115]]

          for b in range(len(b_x)):
            input_x , input_y = b_x[b] , b_y[b] 
            #input_x=cc.convert(input_x)
            input_x = torch.tensor(tokenizer.encode(input_x, add_special_tokens=False)).unsqueeze(0)
            input_y = torch.tensor(input_y).to(device)
            input_x = (input_x).to(device)
            optimizer.zero_grad()
            outputs = model(input_x, labels=input_y)

            loss = outputs[0]
            loss.backward()
            optimizer.step()


            running_loss += loss.item()
         # break

      #print('[epoch %d] loss: %.3f, acc: %.3f' %
      torch.save(model.state_dict(), '/content/drive/My Drive/DataSet/weight/Extend_data_model_state-exm.bin')

In [ ]:
fileName = '/content/drive/My Drive/DataSet/TrainData/ExtendTestDatawwm.csv'
df = pd.read_csv(fileName)

In [ ]:
input_data = df['Content']
label_data = df['label']
tokenizer = BertTokenizer.from_pretrained('hfl/chinese-bert-wwm-ext')
model = BertForTokenClassification.from_pretrained('hfl/chinese-bert-wwm-ext')
train(model,input_data,label_data,50)

epoch 1
['國', '際', '中', '心', '╱', '綜', '合', '報', '導', '香', '港', '民', '政', '事', '務', '局', '前', '局', '長', '也', '是', '資', '深', '影', '星', '胡', '慧', '中', '的', '丈', '夫', '何', '志', '平', '因', '賄', '賂', '非', '洲', '政', '要', '並', '洗', '錢', '，', '因', '此', '遭', '到', '美', '國', '聯', '邦', '法', '院', '判', '刑', '3', '年', '與', '罰', '款', '40', '萬', '美', '金', '（', '約', '1200', '萬', '台', '幣', '）', '，', '從', '去', '年', '3', '月', '起', '入', '監', '服', '刑', '，', '因', '行', '為', '良', '好', '，', '於', '本', '月', '8', '日', '提', '前', '獲', '釋', '，', '據', '了', '解', '，', '何', '志', '平', '將', '被', '遣', '返', '回', '香', '港', '。', '▲', '胡', '慧', '中', '老', '公', '何', '志', '平', '2017', '年', '遭', '逮', '捕', '。', '（', '圖', '╱', '翻', '攝', '自', '微', '博', '）', '綜', '合', '媒', '體', '報', '導', '，', '2014', '年', '起', '何', '志', '平', '以', '香', '港', '中', '華', '能', '源', '基', '金', '會', '秘', '書', '長', '身', '份', '，', '聯', '合', '塞', '內', '加', '爾', '前', '外', '交', '部', '長', '賄', '賂', '查', '德', '總', '統', '及', '烏', '干', '達', '外', '交', '部', '長', '，', '想', '

In [ ]:
model.save_pretrained("/content/drive/My Drive/DataSet/chinese-bert-wwm-ext")


In [ ]:
tokenizer.save_pretrained("/content/drive/My Drive/DataSet/chinese-bert-wwm-ext")


('/content/drive/My Drive/DataSet/chinese-bert-wwm-ext/vocab.txt',
 '/content/drive/My Drive/DataSet/chinese-bert-wwm-ext/special_tokens_map.json',
 '/content/drive/My Drive/DataSet/chinese-bert-wwm-ext/added_tokens.json')